# Working With pandas Dataframes in Databricks
<img src='https://pandas.pydata.org/static/img/pandas.svg' width="400" />

In Databricks, we typically work with Spark dataframes.  They are great for doing distributed computing on a cluster.
However, there are many Python libraries that are not designed for distributed computing.  They use dataframes from the [pandas](https://pandas.pydata.org/)
library.  These datafames are designed to be stored in the memory of a single machine, not distributed across a cluster.

*Is there a way we can distribute pandas-based Python code across a cluster?*

Yes, you can!  Spark 2.3 added a feature called "[Pandas User-Defined Functions](https://databricks.com/blog/2017/10/30/introducing-vectorized-udfs-for-pyspark.html)"
(or "UDF" for short).  This provides the ability to define low-overhead, high-performance UDFs entirely in Python.

Here's how it works:
 - Write a Python function that accepts a pandas dataframe as the input
 - Divide your Spark dataframe into groups using the `groupBy` method
 - Each group will be converted to a pandas dataframe and passed to your function. These will be executed in parallel as each group's processing can occur on a different executor.
 
Let's walk through an example!

## Load Some Data Into Spark
First, we'll make a Spark dataframe.

In [0]:
# Read in sample data from a CSV file and infer the schema
df = spark\
      .read\
      .option("inferSchema", "true")\
      .option("header", "true")\
      .csv("/databricks-datasets/flights/departuredelays.csv")

display(df)

date delay distance origin destination 1011245 6 602 ABE ATL 1020600 -8 369 ABE DTW 1021245 -2 602 ABE ATL 1020605 -4 602 ABE ATL 1031245 -4 602 ABE ATL 1030605 0 602 ABE ATL 1041243 10 602 ABE ATL 1040605 28 602 ABE ATL 1051245 88 602 ABE ATL 1050605 9 602 ABE ATL 1061215 -6 602 ABE ATL 1061725 69 602 ABE ATL 1061230 0 369 ABE DTW 1060625 -3 602 ABE ATL 1070600 0 369 ABE DTW 1071725 0 602 ABE ATL 1071230 0 369 ABE DTW 1070625 0 602 ABE ATL 1071219 0 569 ABE ORD 1080600 0 369 ABE DTW 1081230 33 369 ABE DTW 1080625 1 602 ABE ATL 1080607 5 569 ABE ORD 1081219 54 569 ABE ORD 1091215 43 602 ABE ATL 1090600 151 369 ABE DTW 1091725 0 602 ABE ATL 1091230 -4 369 ABE DTW 1090625 8 602 ABE ATL 1091219 83 569 ABE ORD 1101215 -5 602 ABE ATL 1100600 -5 369 ABE DTW 1101725 7 602 ABE ATL 1101230 -8 369 ABE DTW 1100625 52 602 ABE ATL 1101219 0 569 ABE ORD 1111215 127 602 ABE ATL 1110600 -9 369 ABE DTW 1110625 -4 602 ABE ATL 1121215 -5 602 ABE ATL 1121725 -1 602 ABE ATL 1131215 14 602 ABE ATL 1130600 -7 369 ABE DTW 1131725 -6 602 ABE ATL 1131230 -13 369 ABE DTW 1130625 29 602 ABE ATL 1131219 -8 569 ABE ORD 1140600 -9 369 ABE DTW 1141725 -9 602 ABE ATL 1141230 -8 369 ABE DTW 1140625 -5 602 ABE ATL 1141219 -10 569 ABE ORD 1150600 0 369 ABE DTW 1151725 -6 602 ABE ATL 1151230 0 369 ABE DTW 1150625 0 602 ABE ATL 1150607 0 569 ABE ORD 1151219 0 569 ABE ORD 1161215 -10 602 ABE ATL 1160600 -1 369 ABE DTW 1161725 -6 602 ABE ATL 1161230 -7 369 ABE DTW 1160625 -4 602 ABE ATL 1161219 68 569 ABE ORD 1171215 -8 602 ABE ATL 1170600 -5 369 ABE DTW 1171725 5 602 ABE ATL 1171230 -10 369 ABE DTW 1170625 -6 602 ABE ATL 1171219 -10 569 ABE ORD 1181215 -12 602 ABE ATL 1180600 -13 369 ABE DTW 1180625 0 602 ABE ATL 1191215 -16 602 ABE ATL 1191725 -5 602 ABE ATL 1201215 -8 602 ABE ATL 1201725 -5 602 ABE ATL 1201230 -11 369 ABE DTW 1200625 -7 602 ABE ATL 1201219 -6 569 ABE ORD 1210600 89 369 ABE DTW 1211725 0 602 ABE ATL 1211230 44 369 ABE DTW 1210625 -6 602 ABE ATL 1211219 9 569 ABE ORD 1220600 80 369 ABE DTW 1221230 -5 369 ABE DTW 1220625 333 602 ABE ATL 1220607 219 569 ABE ORD 1221219 15 569 ABE ORD 1231215 -12 602 ABE ATL 1230600 -3 369 ABE DTW 1231725 180 602 ABE ATL 1231230 -5 369 ABE DTW 1230625 -8 602 ABE ATL 1231219 -13 569 ABE ORD 1241215 -11 602 ABE ATL 1240600 -3 369 ABE DTW 1241725 2 602 ABE ATL 1241230 -5 369 ABE DTW 1240625 -3 602 ABE ATL 1241219 0 569 ABE ORD 1251215 2 602 ABE ATL 1250600 -4 369 ABE DTW 1250625 -4 602 ABE ATL 1261215 1 602 ABE ATL 1261725 7 602 ABE ATL 1271215 -4 602 ABE ATL 1270600 -9 369 ABE DTW 1271725 -8 602 ABE ATL 1271230 -7 369 ABE DTW 1270625 -1 602 ABE ATL 1271219 0 569 ABE ORD 1280600 -6 369 ABE DTW 1281725 -3 602 ABE ATL 1281230 -8 369 ABE DTW 1280625 -4 602 ABE ATL 1281219 0 569 ABE ORD 1290600 0 369 ABE DTW 1291230 0 369 ABE DTW 1290625 4 602 ABE ATL 1290607 92 569 ABE ORD 1291219 -10 569 ABE ORD 1301215 0 602 ABE ATL 1300600 -1 369 ABE DTW 1301725 10 602 ABE ATL 1301230 0 369 ABE DTW 1300625 0 602 ABE ATL 1301219 -11 569 ABE ORD 1311215 1 602 ABE ATL 1310600 -4 369 ABE DTW 1311725 25 602 ABE ATL 1311230 -4 369 ABE DTW 1310625 -5 602 ABE ATL 1311219 24 569 ABE ORD 1011400 26 137 ABI DFW 1011525 -11 137 ABI DFW 1021400 -5 137 ABI DFW 1021525 47 137 ABI DFW 1031400 -12 137 ABI DFW 1031525 40 137 ABI DFW 1041400 -12 137 ABI DFW 1041525 3 137 ABI DFW 1051400 -5 137 ABI DFW 1051525 -5 137 ABI DFW 1061400 2 137 ABI DFW 1061525 22 137 ABI DFW 1071400 -12 137 ABI DFW 1071525 -15 137 ABI DFW 1081525 21 137 ABI DFW 1091525 -8 137 ABI DFW 1101525 4 137 ABI DFW 1111525 -23 137 ABI DFW 1121525 -9 137 ABI DFW 1131525 -12 137 ABI DFW 1141525 -5 137 ABI DFW 1151525 -17 137 ABI DFW 1161525 2 137 ABI DFW 1171525 -9 137 ABI DFW 1181525 -5 137 ABI DFW 1191525 -3 137 ABI DFW 1201525 -6 137 ABI DFW 1211525 -17 137 ABI DFW 1221525 40 137 ABI DFW 1231525 -12 137 ABI DFW 1241525 21 137 ABI DFW 1251525 -6 137 ABI DFW 1261525 -12 137 ABI DFW 1271525 -13 137 ABI DFW 1281525 -10 137 ABI DFW 1291525 146 137 ABI DFW 1301525 -13 137 ABI DFW 1311525 6 137 

In [0]:
# In this dataset, flights originated from 255 unique airports
df.select("origin").distinct().count()

Out[2]: 255

In [0]:
# How many flights originated from each airport?
display(df.groupBy("origin").count().sort("origin"))

origin count ABE 448 ABI 706 ABQ 5739 ABY 252 ACT 437 ACV 767 ADQ 132 AEX 878 AGS 724 ALB 1959 ALO 167 AMA 1861 ANC 3632 ATL 91484 ATW 575 AUS 10026 AVL 702 AVP 262 AZO 158 BDL 5342 BET 242 BFL 859 BGR 199 BHM 3289 BIL 766 BIS 453 BMI 688 BNA 13733 BOI 2525 BOS 25348 BPT 257 BQK 249 BQN 340 BRO 610 BRW 229 BTM 180 BTR 2119 BTV 788 BUF 4365 BUR 5079 BWI 21558 BZN 880 CAE 1707 CAK 1645 CDC 154 CDV 178 CEC 244 CHA 904 CHO 302 CHS 2841 CIC 269 CID 1324 CLD 602 CLE 9856 CLL 673 CLT 28402 CMH 6545 CMI 553 COD 179 COS 2231 CPR 532 CRP 1552 CRW 756 CSG 331 CVG 4760 DAB 397 DAL 11272 DAY 2260 DBQ 153 DCA 17109 DEN 53148 DFW 68482 DHN 339 DLH 343 DRO 544 DSM 2497 DTW 23421 EGE 877 EKO 244 ELM 414 ELP 4247 EUG 1271 EVV 679 EWR 27656 EYW 1248 FAI 812 FAR 1219 FAT 2697 FAY 571 FCA 408 FLL 18006 FNT 981 FSD 1664 FSM 600 FWA 877 GEG 2044 GFK 3 GGG 180 GJT 847 GNV 774 GPT 1051 GRB 1109 GRR 2585 GSO 1902 GSP 1788 GTF 425 GTR 250 GUC 245 GUM 90 HDN 522 HLN 364 HNL 11031 HOU 14740 HPN 1777 HRL 1092 HSV 1616 IAD 14136 IAH 43361 ICT 2173 IDA 654 ILM 508 IND 6925 ISP 1370 ITO 1493 JAC 1020 JAN 2124 JAX 5505 JFK 23572 JNU 885 KOA 2657 KTN 540 LAN 312 LAS 33107 LAW 361 LAX 54086 LBB 1532 LCH 515 LEX 1174 LFT 1537 LGA 25458 LGB 2758 LIH 2576 LIT 3354 LNK 548 LRD 582 LSE 154 MAF 2414 MBS 340 MCI 10815 MCO 28313 MDT 1054 MDW 20056 MEM 3730 MFE 1050 MFR 790 MGM 892 MHT 1538 MIA 21817 MKE 8065 MLB 347 MLI 1012 MLU 789 MOB 1414 MOD 270 MOT 392 MQT 77 MRY 1220 MSN 2359 MSO 694 MSP 24031 MSY 10277 MTJ 558 MYR 383 OAJ 390 OAK 10026 OGG 5198 OKC 4935 OMA 4868 OME 177 ONT 4895 ORD 64228 ORF 2861 OTZ 177 PBI 7079 PDX 12889 PHF 508 PHL 18061 PHX 40155 PIA 866 PIH 241 PIT 6945 PNS 1980 PSC 623 PSG 180 PSP 3660 PVD 2895 PWM 1076 RAP 679 RDD 270 RDM 794 RDU 9507 RIC 3800 RNO 3708 ROA 470 ROC 2179 RST 192 RSW 9419 SAN 18005 SAT 8216 SAV 1907 SBA 2380 SBN 991 SBP 1122 SCC 229 SCE 167 SDF 3418 SEA 23078 SFO 39483 SGF 1641 SGU 436 SHV 1672 SIT 269 SJC 9746 SJT 437 SJU 6806 SLC 25868 SMF 9886 SMX 307 SNA 9411 SPS 359 SRQ 1168 STL 12142 STT 1273 STX 251 SUN 319 SUX 167 SWF 180 SYR 1507 TLH 1171 TOL 237 TPA 17084 TRI 536 TUL 4681 TUS 4321 TVC 348 TWF 334 TXK 257 TYR 661 TYS 1951 VLD 253 VPS 1186 WRG 180 XNA 2581 YAK 178 YUM 755

## Create a Python Function

Now we want to create a user-defined function that performs our calculations.  There are two types of pandas UDF's in Spark:  Scalar and Grouped-Map.
Scalar functions accept a single pandas *series* (i.e. a single column).  Grouped-map functions accept a whole pandas dataframe, and they can operate on all of the
data in that dataframe.  We'll be using a grouped-map function for our example.

Grouped-map pandas UDFs are designed for the "split-apply-combine" pattern of data analysis, and they operate on all the data for some group.
(e.g., "for each airport, apply this operation")  Grouped-map pandas UDFs first split a Spark DataFrame into groups based on the conditions specified
in the `groupBy` operator, applies a user-defined function (pandas.DataFrame -> pandas.DataFrame) to each group, and then combines all of the results
into a new Spark DataFrame.

### Declaring the Output Schema
When you declare your Python function as a pandas UDF, you must provide the schema that will be used for the new dataframe that you are creating.  In our case,
we're going to use the structure of the existing dataframe and just add some new columns.  So we can start with the schema of the Spark dataframe and append the
definintions of our new columns.

In [0]:
from pyspark.sql.types import *

# Start with the fields already in the Spark dataframe
output_schema_fields = [f for f in df.schema.fields]

# Add the new fields that we will be creating in our UDF
output_schema_fields.append(StructField("run_id", StringType(), True))
output_schema_fields.append(StructField("hostname", StringType(), True))
output_schema_fields.append(StructField("airport_average_delay", DoubleType(), True))

# Convert the list of fields to a Spark "StructType" schema
output_schema = StructType(output_schema_fields)

### Declaring the Function
When you declare your Python function as a pandas UDF, you must use the `pandas_udf` decorator.  This decorator accepts two parameters: the schema of the output
Spark dataframe (which we just created) and the type of pandas UDF (in our case, "GROUPED_MAP").

Inside the function, you work with the pandas dataframe just like you would in straight Python. You can add or remove columns or rows.  You can even
synthesize the data into a new pandas dataframe with a totally different structure and return that back to Spark.

In our example below, we will do three things:
  1. Compute a new unique string and apply the value as a new column to all rows in the dataset.  This will prove that each grouping is processed separately.
  2. Add a new column with the hostname of the computer that is doing the processing.  This will prove that the computation has been distributed to different machines in the cluster.
  3. Compute the average delay time for the airport as a demonstration of how you can compute using a pandas dataframe
  
Let's write our function!

In [0]:
from pyspark.sql.functions import pandas_udf, PandasUDFType
import uuid
import socket

@pandas_udf(output_schema, PandasUDFType.GROUPED_MAP)
# Input/output are both a pandas.DataFrame
def my_pandas_function(pdf):
  # 1. Compute a guid and assign it as a column to all rows in the pandas dataframe
  my_run_id = str(uuid.uuid4())
  pdf["run_id"] = my_run_id
  
  # 2. Add a new column that contains the name of the computer on which this code is being executed
  pdf["hostname"] = socket.gethostname()
  
  # 3. Compute the average delay for the airport in this grouping and add that as a column to the output pandas dataframe
  pdf["airport_average_delay"] = pdf["delay"].mean()

  return pdf

Now that we have our pandas UDF, we just perform a `groupBy` on our Spark dataframe and then `apply` the UDF to the groupings.  This will run the UDF on each grouping,
collect all the results, and then combine them into a *new* Spark dataframe.

In [0]:
new_df = df.groupBy("origin").apply(my_pandas_function)
display(new_df)

/databricks/spark/python/pyspark/sql/pandas/group_ops.py:100: UserWarning: It is preferred to use 'applyInPandas' over this API. This API will be deprecated in the future releases. See SPARK-28264 for more details.
  warnings.warn(


date delay distance origin destination run_id hostname airport_average_delay 2010635 0 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2011305 9 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2020635 -1 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2021305 -7 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2030635 -11 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2031305 0 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2040635 -1 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2041305 1 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2050635 -7 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2051305 2 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2060635 0 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2061305 40 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2070635 5 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2071305 0 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2080635 -8 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2081305 42 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2090635 -6 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2091305 -4 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2100635 -9 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2101305 0 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2110635 0 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2111305 14 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2120635 -6 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2121305 -2 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2130635 -5 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2131305 -2 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2140635 -4 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2141305 -5 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2150635 -1 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2151305 -8 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2160635 -6 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2161305 -14 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2170635 -4 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2171305 -14 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139-64-8 -0.7666666666666667 2180635 -11 311 BTM SLC e0a6b587-aef5-4354-97bc-b427643989cd 0522-135927-tjhdgp5d-10-139

Now let's run some checks against `new_df` to make sure Spark is processing the data as we expected.  All of the rows for an airport should have been processed by
a single call to the `my_pandas_function` UDF.  Therefore, we would expect all of the rows for each airport to have the same `run_id` value and to have the same
`hostname` value.  We'll use a distinct count to make sure that each airport has only one value for those columns.

In [0]:
from pyspark.sql.functions import *

new_df\
  .groupBy("origin")\
  .agg(
    count("*").alias("row_count"),
    countDistinct("run_id").alias("run_id_count"),
    countDistinct("hostname").alias("hostname_count")
  ).show()

+------+---------+------------+--------------+
|origin|row_count|run_id_count|hostname_count|
+------+---------+------------+--------------+
|   MSY|    10277|           1|             1|
|   GEG|     2044|           1|             1|
|   BUR|     5079|           1|             1|
|   SNA|     9411|           1|             1|
|   GRB|     1109|           1|             1|
|   GTF|      425|           1|             1|
|   IDA|      654|           1|             1|
|   GRR|     2585|           1|             1|
|   PSG|      180|           1|             1|
|   EUG|     1271|           1|             1|
|   PVD|     2895|           1|             1|
|   GSO|     1902|           1|             1|
|   MYR|      383|           1|             1|
|   OAK|    10026|           1|             1|
|   MQT|       77|           1|             1|
|   FAR|     1219|           1|             1|
|   FSM|      600|           1|             1|
|   MSN|     2359|           1|             1|
|   COD|     

Next, since each group of airports was processed separately, we would expect the number of unique `run_id` values to be the same as the number of unique airport codes.
Let's check!

In [0]:
print(new_df.select("origin").distinct().count())
print(new_df.select("run_id").distinct().count())

255
255


We also expect the code to be executed across different machines in the cluster.  If we group by `hostname`, we should see one row for each node in our cluster.  Also, the number of rows processed by each node should be roughly symetrical.

In [0]:
display(new_df.groupBy("hostname").count())

hostname count 0522-135927-tjhdgp5d-10-139-64-4 287311 0522-135927-tjhdgp5d-10-139-64-8 345022 0522-135927-tjhdgp5d-10-139-64-6 345628 0522-135927-tjhdgp5d-10-139-64-7 413617

Lastly, the `airport_average_delay` value should be the same for every row for a given airport.  We can also use Spark to check our math and make sure that the
average was calculated correctly.

In [0]:
new_df\
  .groupBy("origin")\
  .agg(
    min("airport_average_delay").alias("min_avg_delay"),
    max("airport_average_delay").alias("max_avg_delay"),
    avg("delay").alias("avg_computed_by_spark")
  ).show()

+------+-------------------+-------------------+---------------------+
|origin|      min_avg_delay|      max_avg_delay|avg_computed_by_spark|
+------+-------------------+-------------------+---------------------+
|   CDC|0.33116883116883117|0.33116883116883117|  0.33116883116883117|
|   ACT|  0.897025171624714|  0.897025171624714|    0.897025171624714|
|   HPN| 14.065278559369725| 14.065278559369725|   14.065278559369725|
|   RDD| 13.059259259259258| 13.059259259259258|   13.059259259259258|
|   AUS| 10.835627368841013| 10.835627368841013|   10.835627368841013|
|   MLI| 13.699604743083004| 13.699604743083004|   13.699604743083004|
|   SJU| 14.286952688803996| 14.286952688803996|   14.286952688803996|
|   ATW| 14.175652173913043| 14.175652173913043|   14.175652173913043|
|   DHN|   6.95575221238938|   6.95575221238938|     6.95575221238938|
|   AVL|  8.158119658119658|  8.158119658119658|    8.158119658119658|
|   GJT| 2.4332939787485244| 2.4332939787485244|   2.4332939787485244|
|   LG

So there you have it.  Spark allows you to distribute execution of your pure Python functions across a cluster by dividing the data into groups, converting each group
to a pandas dataframe, and then processing the groups in parallel.